In [1]:
import json
import pandas as pd
from openai import OpenAI
from dotenv import dotenv_values
from pycaret.clustering import predict_model, load_model

In [2]:
env = dotenv_values(".env")

openai_client = OpenAI(api_key=env["OPENAI_API_KEY"])

# Wczytujemy dane

In [3]:
df = pd.read_csv('welcome_survey_simple_v1.csv', sep=';')
df.head()

age   edu_level      fav_animals fav_place     gender
0    <18  Podstawowe  Brak ulubionych       NaN    Kobieta
1  25-34     Średnie              Psy  Nad wodą  Mężczyzna
2  45-54      Wyższe              Psy   W lesie  Mężczyzna
3  35-44     Średnie             Koty  W górach  Mężczyzna
4  35-44      Wyższe              Psy  Nad wodą  Mężczyzna

# Ładujemy wytrenowany model

In [4]:
kmeans_pipeline = load_model('welcome_survey_clustering_pipeline_v1')

Transformation Pipeline and Model Successfully Loaded


# Aplikujemy model do danych

In [5]:
df_with_clusters = predict_model(model=kmeans_pipeline, data=df)
df_with_clusters["Cluster"].value_counts()

Cluster
Cluster 1    33
Cluster 2    20
Cluster 3    17
Cluster 5    17
Cluster 0    16
Cluster 4    15
Cluster 7    11
Cluster 6    11
Name: count, dtype: int64

# Stworzymy teraz prompt, który prześlemy do LLM-a w celu znalezienia odpowiednich nazw i opisów dla klastrów

In [6]:
cluster_descriptions = {}
for cluster_id in df_with_clusters['Cluster'].unique():
    cluster_df = df_with_clusters[df_with_clusters['Cluster'] == cluster_id]
    summary = ""
    for column in df_with_clusters:
        if column == 'Cluster':
            continue

        value_counts = cluster_df[column].value_counts()
        value_counts_str = ', '.join([f"{idx}: {cnt}" for idx, cnt in value_counts.items()])
        summary += f"{column} - {value_counts_str}\n"

    cluster_descriptions[cluster_id] = summary

In [9]:
print(cluster_descriptions["Cluster 5"])

age - 45-54: 14, 25-34: 2, unknown: 1, 18-24: 0, 35-44: 0, 55-64: 0, <18: 0, >=65: 0
edu_level - Wyższe: 15, Średnie: 2, Podstawowe: 0
fav_animals - Psy: 15, Koty i Psy: 2, Brak ulubionych: 0, Inne: 0, Koty: 0
fav_place - Nad wodą: 12, Inne: 2, W górach: 0, W lesie: 0
gender - Kobieta: 9, Mężczyzna: 8



In [10]:
prompt = "Użyliśmy algorytmu klastrowania."
for cluster_id, description in cluster_descriptions.items():
    prompt += f"\n\nKlaster {cluster_id}:\n{description}"

prompt += """
Wygeneruj najlepsze nazwy dla każdego z klasterów oraz ich opisy

Użyj formatu JSON. Przykładowo:
{
    "Cluster 0": {
        "name": "Klaster 0",
        "description": "W tym klastrze znajdują się osoby, które..."
    },
    "Cluster 1": {
        "name": "Klaster 1",
        "description": "W tym klastrze znajdują się osoby, które..."
    }
}
"""
print(prompt)

Użyliśmy algorytmu klastrowania.

Klaster Cluster 7:
age - 35-44: 6, >=65: 2, 45-54: 1, <18: 1, unknown: 1, 18-24: 0, 25-34: 0, 55-64: 0
edu_level - Wyższe: 9, Podstawowe: 1, Średnie: 1
fav_animals - Brak ulubionych: 11, Inne: 0, Koty: 0, Koty i Psy: 0, Psy: 0
fav_place - Nad wodą: 3, W lesie: 3, Inne: 0, W górach: 0
gender - Mężczyzna: 7, Kobieta: 3


Klaster Cluster 2:
age - 25-34: 7, 18-24: 5, 35-44: 4, 45-54: 4, 55-64: 0, <18: 0, >=65: 0, unknown: 0
edu_level - Średnie: 20, Podstawowe: 0, Wyższe: 0
fav_animals - Psy: 9, Inne: 5, Koty: 5, Brak ulubionych: 1, Koty i Psy: 0
fav_place - W górach: 13, Nad wodą: 4, W lesie: 2, Inne: 1
gender - Mężczyzna: 20, Kobieta: 0


Klaster Cluster 0:
age - 45-54: 7, 35-44: 5, 25-34: 3, 55-64: 1, 18-24: 0, <18: 0, >=65: 0, unknown: 0
edu_level - Wyższe: 15, Średnie: 1, Podstawowe: 0
fav_animals - Psy: 16, Brak ulubionych: 0, Inne: 0, Koty: 0, Koty i Psy: 0
fav_place - W lesie: 16, Inne: 0, Nad wodą: 0, W górach: 0
gender - Mężczyzna: 11, Kobieta: 5


In [11]:
response = openai_client.chat.completions.create(
    model="gpt-4o",
    temperature=0,
    messages=[
        {
            "role": "user",
            "content": [{"type": "text", "text": prompt}],
        }
    ],
)

In [12]:
result = response.choices[0].message.content.replace("```json", "").replace("```", "").strip()
cluster_names_and_descriptions = json.loads(result)

# Zapisujemy nasze nazwy i opisy klastrów do pliku JSON

In [13]:
with open("welcome_survey_cluster_names_and_descriptions_v1.json", "w") as f:
    f.write(json.dumps(cluster_names_and_descriptions))

# Odczytujemy z naszego pliku JSON - nazwy i opisy klastrów

In [11]:
with open("welcome_survey_cluster_names_and_descriptions_v1.json", "r") as f:
    print(json.loads(f.read()))

{'Cluster 0': {'name': 'Miłośnicy Lasów i Psów', 'description': 'W tym klastrze znajdują się osoby, które preferują spędzanie czasu w lesie i mają wyższe wykształcenie. Większość z nich to mężczyźni w wieku 45-54 lat, a ich ulubionymi zwierzętami są psy.'}, 'Cluster 1': {'name': 'Profesjonaliści Nad Wodą', 'description': 'W tym klastrze znajdują się osoby z wyższym wykształceniem, które preferują spędzanie czasu nad wodą. Większość z nich to mężczyźni w wieku 35-44 lat, a ich ulubionymi zwierzętami są psy.'}, 'Cluster 2': {'name': 'Młodzi Miłośnicy Gór', 'description': 'W tym klastrze znajdują się młodsze osoby z wykształceniem średnim, które preferują spędzanie czasu w górach. Większość z nich to mężczyźni w wieku 25-34 lat, a ich ulubionymi zwierzętami są psy.'}, 'Cluster 3': {'name': 'Wykształceni Miłośnicy Gór', 'description': 'W tym klastrze znajdują się osoby z wyższym wykształceniem, które preferują spędzanie czasu w górach. Większość z nich to mężczyźni w wieku 35-44 lat, a ich